## Bottleneck and Wasserstein distance between persistence diagrams

We will use the Julia package `PersistenceDiagrams` to compute Bottleneck and Wasserstein distances between persistence diagrams and to find corresponding matchings.

We will be using Julia packages `LinearAlgebra`, `Plots`, `PersistenceDiagrams`, and `Ripserer`. Make sure you have these preinstalled.

In [1]:
# Let's load the packages.
using LinearAlgebra, Plots, Ripserer, PersistenceDiagrams

In [ ]:
# We start with the examples we worked out by hand.
# define the points
A = (1, 3); B = (2, 4); C = (1, 2); D = (2, 5); E = (1, Inf)
# first example
# generate the persistence diagrams
X1 = PersistenceDiagram([A]); Y1 = PersistenceDiagram([B])
# compute the bottleneck and Wasserstein distances and corresponding matchings
bottle = Bottleneck()(X1, Y1; matching = true)
water = Wasserstein(1)(X1, Y1; matching = true)
theme(:dark) # optional
plot(plot(bottle; title = ""), plot(water; title = ""))

In [ ]:
# let's compute actual distances
bottle_d = Bottleneck()(X1, Y1; matching = false)
water1_d = Wasserstein(1)(X1, Y1; matching = false)
water2_d = Wasserstein(2)(X1, Y1; matching = false)
bottle_d, water1_d, water2_d

In [ ]:
# second example
X2 = PersistenceDiagram([A, B]); Y2 = PersistenceDiagram([C])
bottle = Bottleneck()(X2, Y2; matching = true)
water = Wasserstein(2)(X2, Y2; matching = true)
plot(plot(bottle; title = "", bottleneck = false), plot(water; title = ""))

In [ ]:
# ... and actual distances
bottle_d = Bottleneck()(X2, Y2; matching = false)
water2_d = Wasserstein(2)(X2, Y2; matching = false)
bottle_d, water2_d

In [ ]:
# third example
X3 = PersistenceDiagram([A, B]); Y3 = PersistenceDiagram([C, D])
bottle = Bottleneck()(X3, Y3; matching = true)
water = Wasserstein(2)(X3, Y3; matching = true)
plot(plot(bottle; title = "", bottleneck = false), plot(water; title = ""))

In [ ]:
# ... and actual distances
bottle_d = Bottleneck()(X3, Y3; matching = false)
water2_d = Wasserstein(2)(X3, Y3; matching = false)
bottle_d, water2_d

In [ ]:
# The returned matching is a dictionary
matching(bottle)

In [ ]:
# fourth example
X4 = PersistenceDiagram([A, E]); Y4 = PersistenceDiagram([C])
bottle = Bottleneck()(X4, Y4; matching = true)
water = Wasserstein(2)(X4, Y4; matching = true)
plot(plot(bottle; title = "", bottleneck = false), plot(water; title = ""))

In [ ]:
# matching weight is infinite in this case
bottle, water

## Comparison of Ripserer's persistence diagrams

In [ ]:
# a function which generates a sample point cloud representing 
# a rectangle [-a, a]x[-b, b] with two circular cutouts
function twoholes((a, b) = (2, 1), (p1, q1, r1) = (-1, 0, 0.5), (p2, q2, r2) = (1, 0, 0.5), num = 800)
    points = NTuple{2,Float64}[]
    num_points = 0
    while num_points <= num
        # a random point in the rectangle [-a, a]x[-b, b]
        point = [2a; 2b].*rand(2, 1) .- [a; b]
        # check if this point is outside both of the circles
        if norm(point - [p1; q1]) >= r1 && norm(point - [p2; q2]) >= r2
            # and add it
            push!(points, Tuple(point))
            num_points += 1
        end
    end
    return points
end

In [ ]:
# first simple example
points1 = twoholes((2, 1), (-1, 0, 0.75), (1, 0, 0.5), 250)
points2 = twoholes((2, 1), (-1, 0, 0.5), (1, 0, 0.75), 500)
diagram1 = ripserer(points1)
diagram2 = ripserer(points2)
theme(:dark) # optional
# let's plot the point clouds and H1 persistence diagrams
cloudplot1 = scatter(points1; aspect_ratio = 1, markercolor = 2, label = false)
cloudplot2 = scatter(points2; aspect_ratio = 1, markercolor = 3, label = false)
persplot1 = plot(diagram1[2]; markercolor = 2, title = "")
persplot2 = plot(diagram2[2]; markercolor = 3, title = "")
plot(cloudplot1, cloudplot2, persplot1, persplot2; layout = (2, 2))

In [ ]:
# those diagrams look similar
bottle = Bottleneck()(diagram1[2], diagram2[2]; matching = true)
water = Wasserstein(1)(diagram1[2], diagram2[2]; matching = true)
plot(plot(bottle; title = "", bottleneck = false), plot(water; title = ""))

In [ ]:
# let's compute actual distances
bottle_d = Bottleneck()(diagram1[2], diagram2[2]; matching = false)
water_d = Wasserstein()(diagram1[2], diagram2[2]; matching = false)
bottle_d, water_d

In [ ]:
# Wasserstein works with the default value of q = 1. We can alter this.
water_d = Wasserstein(2)(diagram1[2], diagram2[2]; matching = false)

In [ ]:
# Let's create an animation object where two circular cutouts move within one rectangle
# and remain fixed in another.

# first rectangle
points1 = twoholes((2, 1), (-1, 0, 0.5), (1, 0, 0.5), 250)
diagram1 = ripserer(points1)
cloudplot1 = scatter(points1; aspect_ratio = 1, markercolor = 2, label = false)
anim = @animate for i in 1:300
    # generate the second rectangle
    points2 = twoholes((2, 1), (1.5-i/100, 0, 0.5), (-1.5+i/100, 0, 0.5), 250)
    # compute persistent homology with Ripserer 
    diagram2 = ripserer(points2)

    # plots of both point clouds and persistence diagrams for H1
    cloudplot2 = scatter(points2; aspect_ratio = 1, markercolor = 3, label = false)

    # bottleneck and Wassestein distances of both diagrams for H1
    bottle = Bottleneck()(diagram1[2], diagram2[2]; matching = true)
    water = Wasserstein(1)(diagram1[2], diagram2[2]; matching = true)
    # ... and their plots
    bottle_plot = plot(bottle; title = "Bottleneck $(round(weight(bottle); digits = 3))", bottleneck = false, lims = (0, 1.5))
    water_plot = plot(water; title = "Wasserstein $(round(weight(water); digits = 3))", lims = (0, 1.5))
    plot(cloudplot1, cloudplot2, bottle_plot, water_plot; layout = (2, 2))
end
gif(anim, fps = 15)